This noteboook uses the SuperBuild of SimpleITK to register a previous subject scan to its corresponding initial reconstruction. The instructions for installing the SuperBuild can be found here:

https://simpleitk.readthedocs.io/en/master/building.html

It is recommended to install the SimpleITK superbuild using a virtual environment. That environment can then be used within a jupyter notebook by adding it as a kernel using the following command:

python -m ipykernel install --user --name=myenv

Where 'myenv' is the name of the environment which contains SimpleITK. The complete instructions for creating and adding a virtual environment in jupyter can be found here:

https://janakiev.com/blog/jupyter-virtual-envs/




In [2]:
import SimpleITK as sitk
import numpy as np
import nibabel as nib
import matplotlib.pyplot as plt
import os

I have created a text file called 'all_files.txt' which contains the pairs of scans that will be registered using this script. The first column of all_files.txt is the previous scan (moving image) and the second column is the initial reconstruction (fixed image). The previous scan will be elastically registered to the initial reconstruction produced in the previous step. 

In [3]:
all_files = np.loadtxt('../data/test_long.txt', dtype=str)
save_path = "../data/reference_reg_10x-varnet/"
os.makedirs(save_path, exist_ok=True)

In [4]:
print(all_files)

[['TUM04-20170309.nii' 'TUM04-20171108.nii' 'TUM04-20180103.nii']
 ['TUM04-20171108.nii' 'TUM04-20190328.nii' 'TUM04-20190523.nii']
 ['TUM04-20180618.nii' 'TUM04-20181009.nii' 'TUM04-20190328.nii']
 ['TUM20-20170928.nii' 'TUM20-20180205.nii' 'TUM20-20180402.nii']
 ['TUM10-20170316.nii' 'TUM10-20171018.nii' 'TUM10-20180122.nii']
 ['TUM10-20171018.nii' 'TUM10-20180122.nii' 'TUM10-20180307.nii']
 ['TUM15-20170531.nii' 'TUM15-20170801.nii' 'TUM15-20170816.nii']]


In [5]:
all_files[0][1]

'TUM04-20171108.nii'

In [7]:
#perform elastic registration for each pair of longitudinal scans
for idx in range(len(all_files)):
    for ii in range(2):
        
        fixed_path = f"../data/predicted/10x-varnet/nib/{all_files[idx][ii+1][:-4]}_predicted.nii" 
        moving_path = f"../../../data/brain-cancer/{all_files[idx][ii]}"
        print('previous scan:', moving_path)
        print('follow-up scan', fixed_path)
        moving = moving_path.split('/')[-1][:-4]
        fixed = fixed_path.split('/')[-1][:-14]

        previous = nib.load(moving_path).get_fdata()
        next_ = nib.load(fixed_path)
        next_affine = next_.affine
        next_ = next_.get_fdata()
        print('shape of fixed image', nib.load(fixed_path).shape)
        print('shape of moving image', nib.load(moving_path).shape)

        # Loading fixed and moving images
        fixed_image = sitk.ReadImage(fixed_path)
        moving_image = sitk.ReadImage(moving_path)

        elastixImageFilter = sitk.ElastixImageFilter()
        elastixImageFilter.SetFixedImage(fixed_image)
        elastixImageFilter.SetMovingImage(moving_image)
        parameterMapVector = sitk.VectorOfParameterMap()
        parameterMapVector.append(sitk.ReadParameterFile("../data/param_files/Par0000affine.txt"))
        parameterMapVector.append(sitk.ReadParameterFile("../data/param_files/Par0000bspline.txt"))

        elastixImageFilter.SetParameterMap(parameterMapVector)
        elastixImageFilter.Execute()

        # Save image as nifti
        registered = elastixImageFilter.GetResultImage()
        reg = sitk.GetArrayFromImage(registered)
        reg = np.swapaxes(reg,0,2)

        name_reg = "elastic_" + moving + "_" + fixed + '-' + str(ii) + '.nii'

        img = nib.Nifti1Image(reg, next_affine)
        nib.save(img, save_path + name_reg)
        sitk.WriteImage(registered,save_path + name_reg)
        print(save_path + name_reg)



previous scan: ../../../data/brain-cancer/TUM04-20170309.nii
follow-up scan ../data/predicted/10x-varnet/nib/TUM04-20171108_predicted.nii
shape of fixed image (512, 512, 156)
shape of moving image (512, 512, 164)
Time spent on saving the results, applying the final transform etc.: 7223 ms.
ELASTIX version: 5.000
Command line options from ElastixBase:
-fMask    unspecified, so no fixed mask used
-mMask    unspecified, so no moving mask used
-out      ./
-threads  unspecified, so all available threads are used
  The default value "true" is used instead.

  From elastix 4.8 it defaults to true!
This may change the behavior of your registrations considerably.

Command line options from TransformBase:
-t0       unspecified, so no initial transform used

Reading images...
Reading images took 0 ms.

  A default pyramid schedule is used.
  A default pyramid schedule is used.
  The default value "GeometricalCenter" is used instead.
Transform parameters are initialized as: [1, 0, 0, 0, 1, 0, 0, 

155	-0.954975	19.199753	2.835370	0.020259	1.0
156	-0.948821	20.199753	2.766550	0.021745	1.1
157	-0.949383	20.076412	2.774857	0.012526	0.9
158	-0.936941	21.075853	2.708945	0.010608	0.8
159	-0.907337	20.952513	2.716909	0.017249	0.8
160	-0.968472	20.829236	2.724916	0.014660	0.9
161	-0.966100	21.829013	2.661307	0.008214	1.0
162	-0.979596	21.846044	2.660250	0.027220	1.1
163	-0.963171	21.722704	2.667930	0.015700	0.9
164	-0.927846	22.722704	2.606910	0.013699	0.8
165	-0.957232	22.599364	2.614285	0.021781	0.8
166	-0.989276	22.551309	2.617170	0.019554	0.8
167	-0.954709	23.551309	2.558425	0.012536	0.8
168	-0.993204	23.427969	2.565527	0.014346	0.8
169	-0.958330	23.385290	2.567994	0.020251	0.8
170	-0.963279	24.385290	2.511412	0.020135	0.8
171	-0.977667	24.674691	2.495500	0.017501	0.8
172	-0.958354	24.551351	2.502257	0.014595	0.9
173	-0.951227	25.544334	2.448873	0.020650	0.8
174	-0.965911	25.424349	2.455202	0.019816	0.8
175	-0.939409	26.424349	2.403431	0.016455	0.8
176	-0.978343	26.301009	2.409699	0

377	-0.943634	106.853276	0.891500	0.015679	0.9
378	-0.984458	106.729943	0.892361	0.017768	0.9
379	-0.934685	107.729943	0.885429	0.015664	2.2
380	-0.991956	107.606603	0.886278	0.020155	0.8
381	-0.944605	107.483263	0.887129	0.015816	0.8
382	-0.931442	108.483263	0.880277	0.013004	0.9
383	-0.965181	109.483263	0.873531	0.013290	0.8
384	-0.932611	110.439328	0.867177	0.018745	0.9
385	-0.961374	110.337393	0.867850	0.016137	0.8
386	-0.933453	110.218465	0.868637	0.010547	0.8
387	-0.983127	110.095125	0.869454	0.020529	0.8
388	-0.978132	111.079825	0.862972	0.011833	0.8
389	-0.952245	112.079825	0.856487	0.018654	0.8
390	-0.969178	111.956485	0.857282	0.017255	0.8
391	-0.958125	111.833144	0.858078	0.007912	0.8
392	-0.942747	112.815533	0.851778	0.016349	0.8
393	-0.939050	113.815427	0.845461	0.013108	0.9
394	-0.959949	114.813782	0.839246	0.014466	0.8
395	-0.967020	114.690537	0.840008	0.021648	0.9
396	-0.940704	114.567211	0.840772	0.028860	1.0
397	-0.953976	114.443871	0.841538	0.012157	0.8
398	-0.973381

167	-0.843637	51.145515	1.033936	0.018567	0.8
168	-0.835991	51.859884	1.023799	0.027885	0.9
169	-0.852846	52.832338	1.010314	0.034156	0.8
170	-0.841240	52.282376	1.017896	0.018625	1.1
171	-0.844099	53.278977	1.004239	0.021221	0.8
172	-0.840831	54.233177	0.991502	0.030918	0.8
173	-0.859259	53.681044	0.998832	0.019201	0.8
174	-0.814340	53.145855	1.006042	0.020674	0.8
175	-0.871226	53.211903	1.005147	0.025211	0.8
176	-0.801140	54.073292	0.993614	0.021300	0.8
177	-0.839582	53.553555	1.000540	0.020455	0.8
178	-0.814843	53.018133	1.007778	0.018683	0.8
179	-0.834296	53.988242	0.994741	0.021547	0.9
180	-0.833932	53.446762	1.001976	0.042071	1.1
181	-0.838879	54.442141	0.988756	0.021486	0.8
182	-0.825690	53.893847	0.995994	0.025112	0.8
183	-0.838469	53.371181	1.002994	0.019115	0.9
184	-0.841018	52.819307	1.010492	0.020703	0.9
185	-0.847255	52.268341	1.018091	0.024461	0.8
186	-0.824244	53.190893	1.005431	0.021010	0.8
187	-0.861975	52.799329	1.010766	0.015211	0.8
188	-0.860722	53.784751	0.997447	0

402	-0.834571	105.073202	0.591671	0.037056	0.8
403	-0.879782	104.521094	0.594273	0.032124	0.9
404	-0.849282	105.507104	0.589642	0.016675	1.9
405	-0.810895	104.954970	0.592226	0.018566	0.8
406	-0.836598	104.743420	0.593223	0.018164	0.8
407	-0.822082	104.191567	0.595838	0.020471	0.9
408	-0.835227	105.115271	0.591474	0.016873	0.8
409	-0.847209	106.106325	0.586862	0.034844	0.9
410	-0.843589	106.838841	0.583499	0.010854	0.8
411	-0.819430	107.544435	0.580296	0.021554	0.8
412	-0.831632	108.131246	0.577659	0.028322	0.9
413	-0.811684	107.579119	0.580140	0.021038	1.4
414	-0.879963	108.442311	0.576271	0.013915	0.8
415	-0.861324	109.395930	0.572057	0.028626	0.9
416	-0.865152	108.845347	0.574482	0.015670	0.9
417	-0.861111	109.790252	0.570332	0.025158	0.9
418	-0.878864	110.548651	0.567044	0.014396	0.9
419	-0.844577	111.498949	0.562977	0.026967	0.8
420	-0.828021	111.763011	0.561857	0.026242	0.8
421	-0.825183	112.762927	0.557657	0.029021	0.9
422	-0.865854	113.723419	0.553681	0.020037	0.9
423	-0.848610

...

1088	-0.757895	142.853501	0.008917	15.4
1089	-0.372438	142.781462	0.005809	15.8
1090	-0.514451	142.709519	0.011914	15.6
1091	-1.060307	142.637674	0.012025	15.8
1092	-0.834404	142.565924	0.008304	15.4
1093	-1.184416	142.494271	0.020756	15.3
1094	-0.670891	142.422714	0.007848	15.3
1095	-0.640334	142.351252	0.008214	15.3
1096	-0.082222	142.279886	0.003057	15.4
1097	-1.106237	142.208616	0.009877	15.4
1098	-0.721051	142.137440	0.012231	15.5
1099	-0.852083	142.066360	0.008577	15.5
1100	-0.761564	141.995374	0.008664	15.3
1101	-0.727776	141.924483	0.008387	15.5
1102	-0.712508	141.853685	0.008856	18.2
1103	-0.605426	141.782983	0.008050	15.8
1104	-0.767151	141.712373	0.014637	15.5
1105	-0.618864	141.641858	0.007306	15.4
1106	-0.589238	141.571436	0.007774	15.5
1107	-0.720014	141.501108	0.011233	15.6
1108	-1.096550	141.430872	0.014461	15.4
1109	-0.250005	141.360730	0.006740	15.4
1110	-0.460520	141.290680	0.006162	15.4
1111	-0.599277	141.220722	0.007627	15.5
1112	-0.658347	141.150857	0.009656	15.4


1296	-0.951744	129.682734	0.010593	15.5
1297	-0.925371	129.627068	0.012453	17.2
1298	-0.722857	129.571466	0.009439	15.6
1299	-0.629517	129.515927	0.006137	15.5
1300	-0.737013	129.460452	0.009041	15.4
1301	-0.157510	129.405040	0.004093	15.4
1302	-0.451905	129.349692	0.007589	15.3
1303	-0.455741	129.294406	0.009505	15.5
1304	-0.374765	129.239183	0.006617	15.5
1305	-0.285056	129.184024	0.006593	15.3
1306	-0.010274	129.128927	0.001587	15.1
1307	-0.787600	129.073892	0.008727	15.4
1308	-0.767860	129.018921	0.013373	15.4
1309	-0.451268	128.964011	0.006413	15.5
1310	-1.028945	128.909164	0.011475	15.7
1311	-0.884500	128.854379	0.013061	15.8
1312	-0.328129	128.799656	0.006430	15.5
1313	-0.622616	128.744995	0.006959	15.4
1314	-1.093894	128.690396	0.022566	15.4
1315	-0.598209	128.635858	0.006736	15.4
1316	-0.074117	128.581382	0.002434	15.5
1317	-0.678850	128.526968	0.007616	15.5
1318	-0.957017	128.472615	0.008758	15.4
1319	-0.615465	128.418323	0.008156	15.4
1320	-0.366072	128.364092	0.005348	15.4


1504	-0.734221	119.320476	0.008906	15.3
1505	-1.012067	119.275893	0.012200	15.9
1506	-0.432977	119.231353	0.006304	15.9
1507	-1.120685	119.186859	0.015727	15.5
1508	-0.542386	119.142408	0.006319	15.4
1509	-1.080327	119.098002	0.011461	15.6
1510	-0.715364	119.053639	0.007263	15.5
1511	-0.639753	119.009321	0.011831	15.3
1512	-0.946248	118.965047	0.015666	15.6
1513	-0.552155	118.920816	0.009343	15.4
1514	-1.095013	118.876630	0.015094	15.4
1515	-0.857404	118.832487	0.010013	15.4
1516	-0.692083	118.788388	0.007958	15.4
1517	-0.172242	118.744332	0.005250	15.5
1518	-0.860584	118.700320	0.010365	15.5
1519	-0.337723	118.656352	0.009481	15.9
1520	-0.365419	118.612427	0.007013	15.6
1521	-0.328910	118.568545	0.006319	15.5
1522	-0.662434	118.524706	0.007437	15.5
1523	-1.132879	118.480911	0.013287	15.3
1524	-0.390711	118.437159	0.006360	15.3
1525	-0.464907	118.393450	0.005945	15.4
1526	-1.121854	118.349784	0.011094	15.5
1527	-0.843976	118.306160	0.008508	15.5
1528	-1.088325	118.262580	0.012127	15.6


1712	-0.759070	110.907603	0.008551	15.5
1713	-1.054684	110.870915	0.014817	15.8
1714	-0.941150	110.834259	0.008437	16.3
1715	-0.705523	110.797636	0.007229	15.5
1716	-1.015721	110.761045	0.010851	15.5
1717	-0.584743	110.724486	0.009110	15.4
1718	-0.886349	110.687959	0.009977	15.4
1719	-0.947610	110.651465	0.009615	15.4
1720	-0.518826	110.615002	0.006937	20.7
1721	-0.847359	110.578572	0.009208	21.0
1722	-0.698377	110.542173	0.009271	21.5
1723	-0.692993	110.505807	0.007264	21.3
1724	-0.518425	110.469472	0.009090	21.2
1725	-1.058962	110.433169	0.014451	20.3
1726	-0.647075	110.396898	0.007506	17.0
1727	-0.646213	110.360659	0.008014	16.4
1728	-0.583648	110.324451	0.006206	15.8
1729	-0.740790	110.288276	0.007951	15.4
1730	-0.430206	110.252131	0.006847	15.5
1731	-0.727224	110.216019	0.006944	15.4
1732	-0.826639	110.179937	0.010035	15.7
1733	-0.440248	110.143888	0.004410	15.5
1734	-0.709617	110.107869	0.008624	15.5
1735	-0.709398	110.071882	0.010588	15.5
1736	-0.508200	110.035927	0.005861	15.8


1918	-1.026608	103.972433	0.011128	15.6
1919	-0.561349	103.941547	0.007422	15.6
1920	-0.915034	103.910686	0.009097	15.7
1921	-1.149191	103.879849	0.013205	15.4
1922	-0.544584	103.849036	0.007371	15.5
1923	-0.960146	103.818248	0.010987	15.4
1924	-0.771051	103.787484	0.007574	15.4
1925	-0.433565	103.756744	0.004960	15.7
1926	-0.793118	103.726029	0.009929	15.4
1927	-0.702919	103.695338	0.009437	15.4
1928	-1.029329	103.664671	0.012243	15.5
1929	-1.111723	103.634028	0.016504	15.5
1930	-0.865823	103.603409	0.012383	15.4
1931	-0.862670	103.572814	0.012002	15.6
1932	-0.671625	103.542244	0.008500	15.7
1933	-0.926512	103.511698	0.010728	15.9
1934	-0.530466	103.481175	0.006983	15.4
1935	-0.663166	103.450677	0.007151	15.3
1936	-0.782632	103.420202	0.009347	15.3
1937	-1.093952	103.389752	0.012077	15.3
1938	-0.456910	103.359325	0.004587	15.4
1939	-0.604605	103.328922	0.006832	15.4
1940	-1.062044	103.298543	0.010721	15.4
1941	-0.833431	103.268188	0.010294	15.5
1942	-0.374830	103.237857	0.006891	15.4
